This script was written to demonstrate Bokeh's interactive HTML graphs. The data I'm using is collected my a function from a previous project; it captures the data table as provided by the Texas Commission on Environmental Quality (TCEQ) for each of the benzene monitoring sits in Houston.

So far the Bokeh chart has the ability to scroll-zoom, box-zoom, pan, show hover text, and toggle site data via the interactive legend.

In [1]:
import pandas as pd #pandas provides most of the data manipulation and scraping tools I need.

sitelist = ['48_039_1607','48_201_0026','48_201_0803', #these are the site codes used by the TCEQ 
            '48_201_0057','48_201_0069','48_201_0617', #to find other site codes, follow one of the links printed below...
            '48_201_1015','48_201_1035','48_201_1039', #...and view the page source. Pollutant codes are also available. 
            '48_201_6000']

def pollutant_puller(pollutant, site, year): #this query grabs data from TCEQ, rearranges is, and prints the TCEQ link
    df = pd.read_html("https://www.tceq.texas.gov/"+ #assembles TCEQ url for site, pollutant, date combination
                  "cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year="
                  +str(year)+"&report_format=web&user_param="+str(pollutant)+
                  "&user_site="+site+"&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1")
    print(site) #prints the site code
    site_name = list(df[1])[6][0] #pulls the site namefrom the TCEQ data table
    pollutant_name = list(df[1])[6][1] #pulls out the actual name of the pollutant (not pollutant code)
    index_values = (['date',0,1,2,3,4,5,6,7,8,9, #aligns time correctly in new DataFrame
                  10,11,12,13,14,15,16,17,18,
                  19,20,21,22,23])
    end_point = (df[1].index[df[1][site_name]['Report year: '+str(year)]['Day']['Day']=='Date']-len(df[1])).tolist()[0]
    pollutant_pivot = df[1].drop(0).iloc[:end_point,:-2]
    pollutant_pivot.columns = index_values
    pollutant_melt = pd.melt(pollutant_pivot, #converts data to a "database" view
                            id_vars = 'date',
                            var_name = 'hour', 
                            value_name = pollutant_name)
    pollutant_melt['year'] = str(year) #defines year
    pollutant_melt['date'] = pollutant_melt['date']+', '+pollutant_melt['year'] #defines date
    pollutant_melt['date'] = pd.to_datetime(pollutant_melt['date']).dt.strftime('%m/%d/%Y') #formats date
    pollutant_melt.sort_values(by=['date','hour'], inplace = True) #makes sure the dates are in order
    pollutant_melt['site'] = site_name #fills in the site name colume
    pollutant_melt #diagnostic step, showed table during development
    #the line below prints a link to the TCEQ the data comes from for verification and troubleshooting
    print("Site_name: "+site_name+"  Pollutant: "+pollutant_name+"   "+"https://www.tceq.texas.gov/"+
                  "cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year="
                  +str(year)+"&report_format=web&user_param="+str(pollutant)+
                  "&user_site="+site+"&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1")
    return(pollutant_melt[['date','hour','site',pollutant_name]])

for site in sitelist: #pulls pollutants for each site in site list
    df = pollutant_puller('45201',site,'2020')
    if 'combined_df' in locals(): #if combined_df already exists, adds new dataframe to the end
        combined_df = combined_df.append(df)
    else:
        combined_df = df #if combined_df doesn't exist, creates dataframe
combined_df['datetime'] = (pd.to_datetime(combined_df['date']) + 
                           pd.to_timedelta(combined_df['hour'], unit = 'h'))
benz_headers = combined_df.columns[combined_df.columns.str.contains('Benzene')]
#combined_df['max_benzene'] = combined_df[list(benz_headers)].max(axis =1)
for reading in list(benz_headers): #this loop combines benzene readings with slightly different names into one column
    combined_df[reading] = pd.to_numeric(combined_df[reading], errors = 'coerce')
combined_df['max_benzene'] = combined_df[list(benz_headers)].max(axis =1)

48_039_1607
Site_name: Oyster Creek [29]  Pollutant: Benzene (POC 1) measured in parts per billion - Volume   https://www.tceq.texas.gov/cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year=2020&report_format=web&user_param=45201&user_site=48_039_1607&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1
48_201_0026
Site_name: Channelview [R]  Pollutant: Benzene (POC 2) measured in parts per billion - Volume   https://www.tceq.texas.gov/cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year=2020&report_format=web&user_param=45201&user_site=48_201_0026&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1


C:\Users\hendr\AppData\Local\Continuum\anaconda3\envs\Air_pollution_Bokeh\lib\site-packages\pandas\core\frame.py:7138: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort,


48_201_0803
Site_name: HRM-3 Haden Road [B] [22]  Pollutant: Benzene (POC 3) measured in parts per billion - Volume   https://www.tceq.texas.gov/cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year=2020&report_format=web&user_param=45201&user_site=48_201_0803&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1
48_201_0057
Site_name: Galena Park A1667 [53] [72]  Pollutant: Benzene (POC 4) measured in parts per billion - Volume   https://www.tceq.texas.gov/cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year=2020&report_format=web&user_param=45201&user_site=48_201_0057&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1
48_201_0069
Site_name: Houston Milby Park A169 [K]  Pollutant: Benzene (POC 2) measured in parts per billion - Volume   https://www.tceq.texas.gov/cgi-bin/compliance/monops/agc_yearly_summary.pl?user_year=2020&report_format=web&user_param=45201&user_site=48_201_0069&user_units=ppb-v&time_format=24hr&first_look=no&submitted=1
48_201_0617
Site_name

The cell below is where are spend some time exploring different Bokeh options.

In [24]:
from bokeh.palettes import Viridis
from bokeh.plotting import figure, output_file, show, output_notebook
from bokeh.models import ColumnDataSource
from datetime import datetime
from bokeh.palettes import Spectral3
from bokeh.palettes import brewer
from bokeh.plotting import figure, show, output_file
from bokeh.sampledata.iris import flowers
from bokeh.models import HoverTool
from bokeh.transform import factor_cmap, factor_mark
from bokeh.layouts import column


output_file('2019071_Benzene_all_houston_sites1600.html')
output_notebook()
_tools_to_show = 'box_zoom,pan,save,hover,reset,tap,wheel_zoom'  
# colors = brewer["Spectral"][len(combined_df['site'].unique())]
# colormap = {i: colors[i] for i in combined_df['site'].unique()}
# colors = [colormap[x] for x in combined_df['site']]

TOOLTIPS = [("Location",'@site'),
            ("Benzene","@max_benzene"),
            ("Date","@date"),
            ("Hour","@hour")]
source = ColumnDataSource(combined_df)
p = figure(x_axis_type="datetime", plot_width=1000, plot_height=400, tools=_tools_to_show, tooltips=TOOLTIPS)
for site, colors in [((combined_df['site'].unique())[i], Viridis[len(combined_df['site'].unique())][i])for i in range(0, len(list(combined_df['site'].unique())))]:
    p.scatter(x = 'datetime', y='max_benzene',source = combined_df[combined_df['site']==site],
             color = colors,
             fill_alpha=0.2, legend_label=site)
# p.scatter("datetime", "Benzene (POC 3) measured in parts per billion - Volume", source=df,
#           fill_alpha=0.4, size=12)
p.legend.location = "top_left"
p.legend.click_policy="hide"

from bokeh.io import output_file, show
from bokeh.models import Dropdown


menu = [("Item 1", "item_1"), ("Item 2", "item_2"), None, ("Item 3", "item_3")]
dropdown = Dropdown(label="Dropdown button", button_type="warning", menu=menu)


show(column(p,dropdown))


Loading BokehJS ...

In [ ]:
[((combined_df['site'].unique())[i], Viridis[len(combined_df['site'].unique())][i])for i in range(0, len(list(combined_df['site'].unique())))]